In [1]:
# !git clone https://github.com/adasegroup/FDS2020_seminars
# !pip install -q open3d trimesh k3d
# %cd FDS2020_seminars/Week\ 7/Day\ 3/

In [2]:
import numpy as np
import open3d as o3d
import matplotlib as mpl
import matplotlib.cm as cm
import matplotlib.pyplot as plt

import os
import sys

sys.path.append('.')
from utils import get_colors, show_points, show_mesh

## PC processing

In [3]:
pcd = o3d.io.read_point_cloud("assets/my_points.txt", format='xyz')
print(pcd)
show_points(np.asarray(pcd.points))

geometry::PointCloud with 4 points.


/Users/albertmatveev/opt/anaconda3/lib/python3.7/site-packages/traittypes/traittypes.py:101: UserWarning: Given trait value dtype "float64" does not match required type "float32". A coerced copy has been created.
  np.dtype(self.dtype).name))


Output()

In [4]:
# generate some neat n times 3 matrix using a variant of sync function
x = np.linspace(-3, 3, 201)
mesh_x, mesh_y = np.meshgrid(x, x)
z = np.sinc((np.power(mesh_x, 2) + np.power(mesh_y, 2)))
z_norm = (z - z.min()) / (z.max() - z.min())
xyz = np.zeros((np.size(mesh_x), 3))
xyz[:, 0] = np.reshape(mesh_x, -1)
xyz[:, 1] = np.reshape(mesh_y, -1)
xyz[:, 2] = np.reshape(z_norm, -1)
print('xyz')
print(xyz)

xyz
[[-3.         -3.          0.17846415]
 [-2.97       -3.          0.17063652]
 [-2.94       -3.          0.16512557]
 ...
 [ 2.94        3.          0.16512557]
 [ 2.97        3.          0.17063652]
 [ 3.          3.          0.17846415]]


In [5]:
# Pass xyz to Open3D.o3d.geometry.PointCloud and visualize
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(xyz)

col = get_colors(np.asarray(pcd.points)[:,-1], cm.jet)

show_points(np.asarray(pcd.points), colors=col, point_size=0.05)

Output()

In [6]:
# Load a ply point cloud, print it, and render it
pcd = o3d.io.read_point_cloud("assets/fragment.ply")
print(pcd)
print(np.asarray(pcd.points))

geometry::PointCloud with 196133 points.
[[0.65234375 0.84686458 2.37890625]
 [0.65234375 0.83984375 2.38430572]
 [0.66737998 0.83984375 2.37890625]
 ...
 [2.00839925 2.39453125 1.88671875]
 [2.00390625 2.39488506 1.88671875]
 [2.00390625 2.39453125 1.88793314]]


In [7]:
print(np.asarray(pcd.colors)[-10:, :])

[[0.77254902 0.71764706 0.69411765]
 [0.98823529 0.97254902 0.95686275]
 [0.72941176 0.68235294 0.6627451 ]
 [0.72941176 0.68235294 0.6627451 ]
 [0.97254902 0.94901961 0.93333333]
 [0.97254902 0.94901961 0.93333333]
 [0.97254902 0.94901961 0.93333333]
 [0.92941176 0.89019608 0.87058824]
 [0.87843137 0.81960784 0.79215686]
 [0.87843137 0.81960784 0.79215686]]


In [8]:
hex_colors = []
for i in np.asarray(pcd.colors):
        hex_colors.append(int(mpl.colors.to_hex(i).replace('#','0x'),16))
hex_colors = np.array(hex_colors, 'uint32')

show_points(np.asarray(pcd.points), colors=hex_colors, point_size=0.007)

Output()

In [9]:
# Downsample the point cloud with a voxel of 0.05
downpcd = pcd.voxel_down_sample(voxel_size=0.05)

hex_colors = []
for i in np.asarray(downpcd.colors):
        hex_colors.append(int(mpl.colors.to_hex(i).replace('#','0x'),16))
hex_colors = np.array(hex_colors, 'uint32')

show_points(np.asarray(downpcd.points), colors=hex_colors, point_size=0.03)

Output()

In [10]:
# Recompute the normal of the downsampled point cloud
downpcd.estimate_normals(search_param=
                         o3d.geometry.KDTreeSearchParamHybrid(radius=0.1,
                                                              max_nn=30))

# Print the normal vectors of the first 10 points
print(np.asarray(downpcd.normals)[:10, :])

[[-0.27566603 -0.89197839 -0.35830543]
 [-0.00694405 -0.99478075 -0.10179902]
 [-0.00399871 -0.99965423 -0.02598917]
 [-0.46344316 -0.68643798 -0.56037785]
 [-0.43476205 -0.62438493 -0.64894177]
 [-0.51440078 -0.56093481 -0.6486478 ]
 [-0.27498453 -0.67317361 -0.68645524]
 [-0.00327304 -0.99977409 -0.02100143]
 [-0.01464332 -0.99960281 -0.02407874]
 [-0.13075895 -0.94176382 -0.30981124]]


In [11]:
show_points(np.asarray(downpcd.points), colors=hex_colors, 
            normals=np.asarray(downpcd.normals)/10, 
            point_size=0.03)

Output()

## Mesh processing and surface reconstruction

In [12]:
# Testing mesh in open3d
mesh = o3d.io.read_triangle_mesh("assets/knot.ply")
print(mesh)
print('Vertices:')
print(np.asarray(mesh.vertices))
print('Triangles:')
print(np.asarray(mesh.triangles))

geometry::TriangleMesh with 1440 points and 2880 triangles.
Vertices:
[[  4.51268387  28.68865967 -76.55680847]
 [  7.63622284  35.52046967 -69.78063965]
 [  6.21986008  44.22465134 -64.82303619]
 ...
 [-22.12651634  31.28466606 -87.37570953]
 [-13.91188431  25.4865818  -86.25827026]
 [ -5.27768707  23.36245346 -81.43279266]]
Triangles:
[[   0   12   13]
 [   0   13    1]
 [   1   13   14]
 ...
 [1438   11 1439]
 [1439   11    0]
 [1439    0 1428]]


In [13]:
show_mesh(np.asarray(mesh.vertices), np.asarray(mesh.triangles))

In [14]:
# load the mesh for surface reconstruction experiments
gt_mesh = o3d.io.read_triangle_mesh("assets/Bunny.ply")

show_mesh(np.asarray(gt_mesh.vertices), np.asarray(gt_mesh.triangles))

In [15]:
pcd = gt_mesh.sample_points_poisson_disk(750)

col = get_colors(np.asarray(pcd.points)[:,2], cm.jet)

show_points(np.asarray(pcd.points), colors=col, point_size=0.002)

Output()

In [16]:
# alpha shape reconstruction
alpha = 0.03
print('alpha = ', alpha)
mesh = o3d.geometry.TriangleMesh.create_from_point_cloud_alpha_shape(pcd, alpha)

show_mesh(np.asarray(mesh.vertices), np.asarray(mesh.triangles))

alpha =  0.03


In [17]:
# alpha shape reconstruction with different alphas
tetra_mesh, pt_map = o3d.geometry.TetraMesh.create_from_point_cloud(pcd)
meshes = []
for alpha in np.logspace(np.log10(0.5), np.log10(0.01), num=4):
    print(f"alpha={alpha:.3f}")
    mesh = o3d.geometry.TriangleMesh.create_from_point_cloud_alpha_shape(
        pcd, alpha, tetra_mesh, pt_map)
    mesh.compute_vertex_normals()
    meshes.append(show_mesh(np.asarray(mesh.vertices), np.asarray(mesh.triangles)))

alpha=0.500
alpha=0.136
alpha=0.037
alpha=0.010


In [18]:
meshes[3]

In [20]:
# prepare point cloud for poisson reconstruction with mesh normals
gt_mesh.compute_vertex_normals()

pcd = gt_mesh.sample_points_poisson_disk(3000)

col = get_colors(np.asarray(pcd.points)[:, 2], cm.jet)

show_points(np.asarray(pcd.points), colors=col, point_size=0.002, 
            normals=np.asarray(pcd.normals)/200)

Output()

In [21]:
mesh, densities = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(pcd, depth=9)

In [22]:
show_mesh(np.asarray(mesh.vertices), np.asarray(mesh.triangles))

In [25]:
# prepare point cloud for poisson reconstruction with estimated normals
gt_mesh = o3d.io.read_triangle_mesh("assets/Bunny.ply")

pcd = gt_mesh.sample_points_poisson_disk(3000)
pcd.estimate_normals(search_param=o3d.geometry.KDTreeSearchParamHybrid(radius=0.1, max_nn=30))

col = get_colors(np.asarray(pcd.points)[:, 2], cm.jet)

show_points(np.asarray(pcd.points), colors=col, point_size=0.002, 
            normals=np.asarray(pcd.normals)/200)

Output()

In [26]:
mesh, densities = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(pcd, depth=9)
show_mesh(np.asarray(mesh.vertices), np.asarray(mesh.triangles))